In [1]:
import numpy as np
import xarray as xr
import matplotlib as mpl
#mpl.use('Agg') # Must be before importing matplotlib.pyplot or pylab!
import matplotlib.pyplot as plt
import matplotlib.ticker as ticker

import pandas as pd
import os
#import seaborn as sns
import timeit
#start_time = timeit.default_timer()
from datetime import datetime,timedelta
from dask.diagnostics import ProgressBar
from functools import partial

In [2]:
ProgressBar().register()

In [3]:
#%% plot parameters
mpl.rcParams['axes.linewidth'] = 2.0 #set the value globally
plt.rc('font', family='serif',size = 18)  # controls default text layout
plt.rc('axes', titlesize=18)     # fontsize of the axes title
plt.rc('axes', labelsize=18)    # fontsize of the x and y labels
plt.rc('xtick', labelsize=18)    # fontsize of the tick labels
plt.rc('ytick', labelsize=18)    # fontsize of the tick labels
plt.rc('legend', fontsize=18)    # legend fontsize
plt.rc('figure', titlesize=18)  # fontsize of the figure title

#sns.set()

plt.rc('text', usetex=False)


In [4]:
def _subset_process_time(ds,var,iop):
    
    #subset for the variable(s)
    ds = ds[var]
    ds['time'] = ds.time.dt.round('T')
    #IOP02
    if iop=='iop02': ds['time'] = pd.to_datetime('2019-08-23') + ds['time'].values
    #IOP03
    if iop=='iop03': ds['time'] = pd.to_datetime('2019-09-24') + ds['time'].values
    return(ds)

def _process_time(ds,iop):
    #round time to the nearest minute (30minute for PALM output)
    ds['time'] = ds.time.dt.round('T')
    #IOP02
    if iop=='iop02':ds['time'] = pd.to_datetime('2019-08-23') + ds['time'].values
    #IOP03
    if iop=='iop03':ds['time'] = pd.to_datetime('2019-09-24') + ds['time'].values    
    return(ds)

#function to concatenate all files for an ensemble member and if needed read in all ensemble members
def open_concat_member_files(ensemble_numbers,file,iop):
    data_list = []
    #loop through ensemble members
    if np.size(ensemble_numbers) > 1:
        for member_num in ensemble_numbers:    

            start_time = timeit.default_timer()
            if iop=='iop02': source_folder = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP2/ensemble.member.'+str(member_num) 
            #file = 'DATA_3D_AV_NETCDF_N02slice' 

            #Make a folder list and read in all the files from those folders. 
            folder_list = os.listdir(source_folder) 
            folder_list.sort() 
            file_list = [] 
            for folder in folder_list: 
                file_list.append(source_folder + '/' +folder+'/'+file) 
            file_list.sort()
            print(folder_list)

            #combine all the data along the time dimenstion 
            #don't combine them sequentially, but infer the sequence from coordinate values 
            #do this in parallel 
            #pull in only those values with a time dimension 
            var = ['w','theta','q','wtheta','wq']
            partial_func = partial(_subset_process_time, var=var,iop=iop)
            ds = xr.open_mfdataset(file_list,preprocess=partial_func) 
            ds.close() 
            print('Member',str(member_num),'finished collecting data')    
            #subset for time and day and collect into another list
            #for day1
            data_list.append(ds)
            elapsed = timeit.default_timer() - start_time
            print('Done with member',str(member_num),' Time elapsed ',elapsed, 'seconds')
        return(data_list)
            
    else:
        member_num =ensemble_numbers

        #loop through ensemble members
        start_time = timeit.default_timer()
        #IOP02
        if iop=='iop02':source_folder = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP2/ensemble.member.'+str(member_num) 
        #IOP03
        if iop=='iop03':source_folder = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP03/OUTPUT/ensemble.member.'+str(member_num) 
        
        #file = 'DATA_3D_AV_NETCDF_N03slice' 
        #file = 'DATA_1D_PR_NETCDF_N02slice' 

        #Make a folder list and read in all the files from those folders. 
        folder_list = os.listdir(source_folder) 
        folder_list.sort() 
        file_list = [] 
        for folder in folder_list: 
            file_list.append(source_folder + '/' +folder+'/'+file) 
        file_list.sort()
        print(folder_list)
        
        #combine all the data along the time dimenstion 
        partial_func = partial(_process_time,iop=iop)    
        ds = xr.open_mfdataset(file_list,preprocess=partial_func) 
        ds.close() 
        print('Member',str(member_num),'finished collecting data')    
        #subset for time and day and collect into another list
        #for day1
        #data_list.append(ds)
        elapsed = timeit.default_timer() - start_time
        print('Done with member',str(member_num),' Time elapsed ',elapsed, 'seconds')
        return(ds)




In [5]:
#set input forcing data to be read
#IOP02
ches_dynamic = '/bog/incoming/CHEESEHEAD/palm/realistic_runs/ches_IOP2/INPUT/ches_IOP2_dynamic'
#ches_dynamic = '/bog/incoming/CHEESEHEAD/palm/realistic_runs/ches_IOP03/INPUT/ches_IOP3_dynamic'

ches_dynamic_ds_IOP2 = xr.open_dataset(ches_dynamic)
ches_dynamic_ds_IOP2.close()
# #assign a time coordinate with units as datetime
# ches_dynamic_ds_IOP2 = ches_dynamic_ds_IOP2.assign_coords(date_time=('time',pd.to_datetime(ches_dynamic_ds_IOP2['time']*1E9,origin=pd.Timestamp('2019-08-23'))))
# #ches_dynamic_ds_IOP2 = ches_dynamic_ds_IOP2.assign_coords(date_time=('time',pd.to_datetime(ches_dynamic_ds_IOP2['time']*1E9,origin=pd.Timestamp('2019-09-24'))))
# #set the new dimension along the old 'time' dimension so that we can plot all the data variables along the new dimension
# ches_dynamic_ds_IOP2.swap_dims({"time": "date_time"})
# ches_dynamic_ds_IOP2

In [15]:
ches_dynamic_ds_IOP2.z.values

array([   6.        ,   18.        ,   30.        ,   42.        ,
         54.        ,   66.        ,   78.        ,   90.        ,
        102.        ,  114.        ,  126.        ,  138.        ,
        150.        ,  162.        ,  174.        ,  186.        ,
        198.        ,  210.        ,  222.        ,  234.        ,
        246.        ,  258.        ,  270.        ,  282.        ,
        294.        ,  306.        ,  318.        ,  330.        ,
        342.        ,  354.        ,  366.        ,  378.        ,
        390.        ,  402.        ,  414.        ,  426.        ,
        438.        ,  450.        ,  462.        ,  474.        ,
        486.        ,  498.        ,  510.        ,  522.        ,
        534.        ,  546.        ,  558.        ,  570.        ,
        582.        ,  594.        ,  606.        ,  618.        ,
        630.        ,  642.        ,  654.        ,  666.        ,
        678.        ,  690.        ,  702.        ,  714.     

In [7]:
ensemble_member_ds_2_P = open_concat_member_files(2,'DATA_3D_AV_NETCDFslice','iop02')


['01.ches_IOP2.20255', '02.ches_IOP2.13449', '03.ches_IOP2.733', '04.ches_IOP2.18198', '05.ches_IOP2.19794', '06.ches_IOP2.11638', '07.ches_IOP02.31113']
Member 2 finished collecting data
Done with member 2  Time elapsed  3.7818468883633614 seconds


In [17]:
ensemble_member_ds_2_P.zu_3d.values[1:]

array([   6.        ,   18.        ,   30.        ,   42.        ,
         54.        ,   66.        ,   78.        ,   90.        ,
        102.        ,  114.        ,  126.        ,  138.        ,
        150.        ,  162.        ,  174.        ,  186.        ,
        198.        ,  210.        ,  222.        ,  234.        ,
        246.        ,  258.        ,  270.        ,  282.        ,
        294.        ,  306.        ,  318.        ,  330.        ,
        342.        ,  354.        ,  366.        ,  378.        ,
        390.        ,  402.        ,  414.        ,  426.        ,
        438.        ,  450.        ,  462.        ,  474.        ,
        486.        ,  498.        ,  510.        ,  522.        ,
        534.        ,  546.        ,  558.        ,  570.        ,
        582.        ,  594.        ,  606.        ,  618.        ,
        630.        ,  642.        ,  654.        ,  666.        ,
        678.        ,  690.        ,  702.        ,  714.     

In [18]:
ensemble_member_ds_2_P.zu_3d.values[1:-1] - ches_dynamic_ds_IOP2.z.values

array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0.